# US News World Report Fairness
## Multiple Optimal Solutions and Equity of Attention

In [1]:
%matplotlib inline
%load_ext autoreload
%autoreload 2

In [2]:
import pandas as pd
import numpy as np

In [3]:
import networkx as nx
from networkx.drawing.nx_agraph import graphviz_layout, to_agraph
import pygraphviz as pgv

from IPython.display import Image
def draw(A):
    return Image(A.draw(format='png', prog='dot'))

In [4]:
import sys
from pathlib import Path
home = str(Path.home())

sys.path.insert(0,"%s/ranking_toolbox"%home)
sys.path.insert(0,"%s/RPLib"%home)
sys.path.insert(0,"%s/fairness_analysis"%home)

In [5]:
import pyrankability

In [6]:
import pyrplib

In [7]:
import equity_of_attention.common

In [18]:
class Details:
    def __init__(self, **entries):
        self.__dict__.update(entries)
        
import joblib
Ds = joblib.load('results/Ds.joblib.z')
D = Ds.loc[(2002,'Both'),'D']
D

Amherst College  Bowdoin College  Carleton College  \
School Name1                                                                    
Amherst College                        0.0              5.0               4.0   
Bowdoin College                        1.0              0.0               4.0   
Carleton College                       2.0              2.0               0.0   
Claremont McKenna College              0.0              2.0               3.0   
Davidson College                       1.0              1.0               3.0   
Haverford College                      1.0              3.0               4.0   
Middlebury College                     3.0              4.0               4.0   
Pomona College                         2.0              3.0               4.0   
Swarthmore College                     3.0              5.0               5.0   
Wellesley College                      0.0              1.0               3.0   
Williams College                       2.0              5.0               4.0   

                           Claremont McKenna College  Davidson College  \
School Name1                                                             
Amherst College                                  6.0               5.0   
Bowdoin College                                  4.0               5.0   
Carleton College                                 3.0               3.0   
Claremont McKenna College                        0.0               4.0   
Davidson College                                 2.0               0.0   
Haverford College                                2.0               5.0   
Middlebury College                               5.0               4.0   
Pomona College                                   3.0               4.0   
Swarthmore College                               6.0               5.0   
Wellesley College                                2.0               2.0   
Williams College                                 5.0               5.0   

                           Haverford College  Middlebury College  \
School Name1                                                       
Amherst College                          5.0                 3.0   
Bowdoin College                          3.0                 2.0   
Carleton College                         2.0                 2.0   
Claremont McKenna College                4.0                 1.0   
Davidson College                         1.0                 2.0   
Haverford College                        0.0                 3.0   
Middlebury College                       3.0                 0.0   
Pomona College                           4.0                 3.0   
Swarthmore College                       4.0                 4.0   
Wellesley College                        0.0                 1.0   
Williams College                         4.0                 3.0   

                           Pomona College  Swarthmore College  \
School Name1                                                    
Amherst College                       4.0                 3.0   
Bowdoin College                       3.0                 1.0   
Carleton College                      2.0                 1.0   
Claremont McKenna College             3.0                 0.0   
Davidson College                      2.0                 1.0   
Haverford College                     2.0                 2.0   
Middlebury College                    3.0                 2.0   
Pomona College                        0.0                 2.0   
Swarthmore College                    4.0                 0.0   
Wellesley College                     1.0                 0.0   
Williams College                      3.0                 2.0   

                           Wellesley College  Williams College  
School Name1                                                    
Amherst College                          6.0               4.0  
Bowdoin College                          5.0               1.0  
Carleton College   

In [19]:
Ds.keys()

Index(['D', 'delta_cont', 'delta_bin', 'details_cont', 'details_bin',
       'details_fixed_cont_x_maximize', 'details_fixed_cont_x_minimize',
       'details_pair_maximize', 'details_pair_minimize'],
      dtype='object')

## Get all optimal solutions

In [9]:
_,details_lop_with_models = pyrankability.rank.solve(D,method='lop',include_model=True)
model = details_lop_with_models['model']
model_file = pyrankability.common.write_model(model)
solution_file = model_file + ".solutions"
!sed -i '/^OBJSENS/d' $model_file
!$home/ranking_toolbox/collect.sh "$model_file" "$solution_file"

opt_k = details_lop_with_models['obj']

solutions = pd.read_csv(solution_file,sep=', ')
x_columns = solutions.columns[1:-1]
xs = []
a,b,c = 1,1,-2*len(x_columns)
n = int((-b + np.sqrt(b**2 - 4*a*c))/(2*a) + 1)
xstar = np.zeros((n,n))
objs = []
s = 0
for k in range(solutions.shape[0]):
    x = np.zeros((n,n))
    for c in x_columns:
        ij_str = c.replace("x(","").replace(")","")
        i,j = ij_str.split(",")
        i,j = int(i),int(j)
        x[i,j] = solutions.loc[k,c]
        x[j,i] = 1 - x[i,j]
    obj = np.sum(np.sum(D*x))
    xs.append(x)
    objs.append(obj)
    error = obj - opt_k
    xstar += x
xstar = xstar/solutions.shape[0]

perms = []
for x in xs:
    r = np.sum(x,axis=0)
    perm = np.argsort(r)
    perms.append(perm)

Restricted license - for non-production use only - expires 2022-01-13
Model file: /tmp/tmp_sav0n_a/model.mps
Solutions file: /tmp/tmp_sav0n_a/model.mps.solutions
SCIP version 7.0.0 [precision: 8 byte] [memory: block] [mode: optimized] [LP solver: SoPlex 5.0.0] [GitHash: 0bc4dc9c65]
Copyright (C) 2002-2020 Konrad-Zuse-Zentrum fuer Informationstechnik Berlin (ZIB)

External codes: 
  SoPlex 5.0.0         Linear Programming Solver developed at Zuse Institute Berlin (soplex.zib.de) [GitHash: 6535a3c8]
  CppAD 20180000.0     Algorithmic Differentiation of C++ algorithms developed by B. Bell (www.coin-or.org/CppAD)
  ZLIB 1.2.11          General purpose compression library by J. Gailly and M. Adler (zlib.net)
  GMP 6.2.0            GNU Multiple Precision Arithmetic Library developed by T. Granlund (gmplib.org)
  ZIMPL 3.3.9          Zuse Institute Mathematical Programming Language developed by T. Koch (zimpl.zib.de)
  PaPILO 1.0.0         parallel presolve for integer and linear optimization

/opt/tljh/user/lib/python3.7/site-packages/ipykernel_launcher.py:10: ParserWarning: Falling back to the 'python' engine because the 'c' engine does not support regex separators (separators > 1 char and different from '\s+' are interpreted as regex); you can avoid this warning by specifying engine='python'.
  # Remove the CWD from sys.path while we load stuff.


In [10]:
print('Number of optimal solutions:',len(perms))

Number of optimal solutions: 72


In [11]:
pd.DataFrame(xstar)

0         1         2         3         4    5         6         7   \
0   0.000000  1.000000  1.000000  1.000000  1.000000  1.0  0.833333  1.000000   
1   0.000000  0.000000  1.000000  1.000000  1.000000  1.0  0.000000  0.416667   
2   0.000000  0.000000  0.000000  0.000000  0.333333  0.0  0.000000  0.000000   
3   0.000000  0.000000  1.000000  0.000000  1.000000  1.0  0.000000  0.208333   
4   0.000000  0.000000  0.666667  0.000000  0.000000  0.0  0.000000  0.000000   
5   0.000000  0.000000  1.000000  0.000000  1.000000  0.0  0.000000  0.000000   
6   0.166667  1.000000  1.000000  1.000000  1.000000  1.0  0.000000  0.750000   
7   0.000000  0.583333  1.000000  0.791667  1.000000  1.0  0.250000  0.000000   
8   0.583333  1.000000  1.000000  1.000000  1.000000  1.0  1.000000  1.000000   
9   0.000000  0.000000  0.333333  0.000000  0.000000  0.0  0.000000  0.000000   
10  0.000000  1.000000  1.000000  1.000000  1.000000  1.0  0.416667  0.708333   

          8         9         10  
0   0.416667  1.000000  1.000000  
1   0.000000  1.000000  0.000000  
2   0.000000  0.666667  0.000000  
3   0.000000  1.000000  0.000000  
4   0.000000  1.000000  0.000000  
5   0.000000  1.000000  0.000000  
6   0.000000  1.000000  0.583333  
7   0.000000  1.000000  0.291667  
8   0.000000  1.000000  1.000000  
9   0.000000  0.000000  0.000000  
10  0.000000  1.000000  0.000000

## Since we know all optimal solutions, we know the true attention of each item

In [12]:
num_items = len(perms[0])
num_rankings = len(perms)
item_relevances = np.zeros((num_rankings,num_items))
for i in range(num_rankings):
    ranking = np.argsort(perms[i])
    item_relevances[i,:] = (num_items - ranking)/num_items
    item_relevances[i,:] = item_relevances[i,:]/np.sum(item_relevances[i,:])
    
true_attentions = np.zeros((num_rankings,num_items))
position_attentions = \
    equity_of_attention.common.calc_position_attentions(num_items, click_probability=0.5, position_cutoff=num_items)
position_attentions = position_attentions/np.sum(position_attentions)
for i in range(num_rankings):
    order = np.argsort(-1*item_relevances[i,:])
    true_attentions[i,:] = position_attentions[order]
true_attention = np.mean(true_attentions,axis=0)
true_attention

array([0.20957499, 0.21055203, 0.08679368, 0.00364354, 0.10643625,
       0.15974597, 0.05031754, 0.01563263, 0.06253053, 0.05243446,
       0.04233838])

In [13]:
pd.DataFrame(item_relevances)

0         1         2         3         4         5         6   \
0   0.151515  0.090909  0.015152  0.075758  0.045455  0.060606  0.106061   
1   0.166667  0.090909  0.015152  0.075758  0.045455  0.060606  0.106061   
2   0.151515  0.090909  0.015152  0.075758  0.045455  0.060606  0.106061   
3   0.166667  0.090909  0.015152  0.075758  0.045455  0.060606  0.106061   
4   0.151515  0.090909  0.030303  0.075758  0.045455  0.060606  0.106061   
..       ...       ...       ...       ...       ...       ...       ...   
67  0.166667  0.090909  0.030303  0.075758  0.045455  0.060606  0.136364   
68  0.166667  0.090909  0.045455  0.075758  0.030303  0.060606  0.136364   
69  0.136364  0.090909  0.015152  0.075758  0.045455  0.060606  0.151515   
70  0.151515  0.090909  0.015152  0.075758  0.045455  0.060606  0.136364   
71  0.166667  0.090909  0.015152  0.075758  0.045455  0.060606  0.136364   

          7         8         9         10  
0   0.121212  0.166667  0.030303  0.136364  
1   0.121212  0.151515  0.030303  0.136364  
2   0.136364  0.166667  0.030303  0.121212  
3   0.136364  0.151515  0.030303  0.121212  
4   0.121212  0.166667  0.015152  0.136364  
..       ...       ...       ...       ...  
67  0.121212  0.151515  0.015152  0.106061  
68  0.121212  0.151515  0.015152  0.106061  
69  0.121212  0.166667  0.030303  0.106061  
70  0.121212  0.166667  0.030303  0.106061  
71  0.121212  0.151515  0.030303  0.106061  

[72 rows x 11 columns]

In [14]:
pd.DataFrame(true_attentions)

0         1         2         3         4         5         6   \
0   0.001954  0.500244  0.000489  0.003908  0.007816  0.250122  0.062531   
1   0.500244  0.001954  0.000489  0.003908  0.007816  0.250122  0.062531   
2   0.001954  0.500244  0.003908  0.000489  0.007816  0.250122  0.062531   
3   0.500244  0.001954  0.003908  0.000489  0.007816  0.250122  0.062531   
4   0.001954  0.500244  0.000489  0.003908  0.007816  0.250122  0.062531   
..       ...       ...       ...       ...       ...       ...       ...   
67  0.500244  0.001954  0.007816  0.003908  0.000489  0.250122  0.062531   
68  0.500244  0.001954  0.007816  0.003908  0.000489  0.250122  0.062531   
69  0.001954  0.007816  0.500244  0.003908  0.000489  0.250122  0.062531   
70  0.001954  0.500244  0.007816  0.003908  0.000489  0.250122  0.062531   
71  0.500244  0.001954  0.007816  0.003908  0.000489  0.250122  0.062531   

          7         8         9         10  
0   0.015633  0.031265  0.000977  0.125061  
1   0.015633  0.031265  0.000977  0.125061  
2   0.015633  0.031265  0.000977  0.125061  
3   0.015633  0.031265  0.000977  0.125061  
4   0.015633  0.031265  0.125061  0.000977  
..       ...       ...       ...       ...  
67  0.015633  0.031265  0.125061  0.000977  
68  0.015633  0.125061  0.031265  0.000977  
69  0.015633  0.031265  0.000977  0.125061  
70  0.015633  0.031265  0.000977  0.125061  
71  0.015633  0.031265  0.000977  0.125061  

[72 rows x 11 columns]

In [15]:
colleges_of_interest = list(D.columns)
colleges_of_interest

['Amherst College',
 'Bowdoin College',
 'Carleton College',
 'Claremont McKenna College',
 'Davidson College',
 'Haverford College',
 'Middlebury College',
 'Pomona College',
 'Swarthmore College',
 'Wellesley College',
 'Williams College']

## Now calculate unfairness if each of the optimal rankings are returned

In [16]:
def calc_unfairness(position_attentions,true_attention,item_relevances,category):
    num_items = len(position_attentions)
    accumulated_attention = np.zeros(num_items) # A
    accumulated_relevance = np.zeros(num_items) # R
    unfairness = []
    iterations = []
    for ranking_num in range(len(item_relevances)):
        iterations.append(ranking_num)
        item_r = item_relevances[ranking_num,:]
        order = np.argsort(-1*item_r)
        accumulated_attention += position_attentions[order]
        accumulated_relevance += true_attention
        unfairness.append(np.abs(accumulated_attention-accumulated_relevance))
    df = pd.DataFrame([unfairness]).T
    df.columns = ["Unfairness"]
    df["Category"] = category
    df["Iteration"] = iterations
    return df.set_index(["Category","Iteration"])

In [17]:
results = pd.DataFrame(columns=["Unfairness","Category","Iteration"]).set_index(["Category","Iteration"])

In [30]:
perm_pair_minimize_x = Ds.loc[(2002,'Both'),'details_pair_minimize'].perm_x
perm_pair_minimize_y = Ds.loc[(2002,'Both'),'details_pair_minimize'].perm_y
pair_item_relevances = np.zeros((num_rankings,num_items))
for i in range(num_rankings):
    if i % 2 == 0:
        ranking = np.argsort(perm_pair_minimize_x)
    else:
        ranking = np.argsort(perm_pair_minimize_y)
    pair_item_relevances[i,:] = (num_items - ranking)/num_items
    pair_item_relevances[i,:] = pair_item_relevances[i,:]/np.sum(pair_item_relevances[i,:])
results = results.append(calc_unfairness(position_attentions,true_attention,pair_item_relevances,"3. Closest Pair"))


In [31]:
perm_pair_maximize_x = Ds.loc[(2002,'Both'),'details_pair_maximize'].perm_x
perm_pair_maximize_y = Ds.loc[(2002,'Both'),'details_pair_maximize'].perm_y
pair_item_relevances = np.zeros((num_rankings,num_items))
for i in range(num_rankings):
    if i % 2 == 0:
        ranking = np.argsort(perm_pair_maximize_x)
    else:
        ranking = np.argsort(perm_pair_maximize_y)
    pair_item_relevances[i,:] = (num_items - ranking)/num_items
    pair_item_relevances[i,:] = pair_item_relevances[i,:]/np.sum(pair_item_relevances[i,:])
results = results.append(calc_unfairness(position_attentions,true_attention,pair_item_relevances,"4. Farthest Pair"))

In [32]:
Ds.columns

Index(['D', 'delta_cont', 'delta_bin', 'details_cont', 'details_bin',
       'details_fixed_cont_x_maximize', 'details_fixed_cont_x_minimize',
       'details_pair_maximize', 'details_pair_minimize'],
      dtype='object')

In [33]:
perm_pair_maximize_x = Ds.loc[(2002,'Both'),'details_fixed_cont_x_minimize'].perm
perm_pair_maximize_y = Ds.loc[(2002,'Both'),'details_fixed_cont_x_maximize'].perm
pair_item_relevances = np.zeros((num_rankings,num_items))
for i in range(num_rankings):
    if i % 2 == 0:
        ranking = np.argsort(perm_pair_maximize_x)
    else:
        ranking = np.argsort(perm_pair_maximize_y)
    pair_item_relevances[i,:] = (num_items - ranking)/num_items
    pair_item_relevances[i,:] = pair_item_relevances[i,:]/np.sum(pair_item_relevances[i,:])
results = results.append(calc_unfairness(position_attentions,true_attention,pair_item_relevances,"2. Nearest and Farthest Pair"))

In [34]:
perm1 = Ds.loc[(2002,'Both'),'details_fixed_cont_x_minimize'].perm
perm2 = Ds.loc[(2002,'Both'),'details_fixed_cont_x_maximize'].perm
perm3 = Ds.loc[(2002,'Both'),'details_pair_maximize'].perm_x
perm4 = Ds.loc[(2002,'Both'),'details_pair_maximize'].perm_y
perm5 = Ds.loc[(2002,'Both'),'details_pair_minimize'].perm_x
perm6 = Ds.loc[(2002,'Both'),'details_pair_minimize'].perm_y
pair_item_relevances = np.zeros((num_rankings,num_items))
c = 0
for i in range(num_rankings):
    if c == 0:
        ranking = np.argsort(perm1)
    elif c == 1:
        ranking = np.argsort(perm2)
    elif c == 2:
        ranking = np.argsort(perm3)
    elif c == 3:
        ranking = np.argsort(perm4)
    elif c == 4:
        ranking = np.argsort(perm6)
    else:
        ranking = np.argsort(perm6)
    c += 1
    if c > 5:
        c = 0
    pair_item_relevances[i,:] = (num_items - ranking)/num_items
    pair_item_relevances[i,:] = pair_item_relevances[i,:]/np.sum(pair_item_relevances[i,:])
results = results.append(calc_unfairness(position_attentions,true_attention,pair_item_relevances,"5. Cycle through 6"))

In [35]:
results = results.append(calc_unfairness(position_attentions,true_attention,item_relevances,"6. All Optimal Solutions"))

single_averaged = None
for i in range(len(item_relevances)):
    rep = []
    for j in range(len(item_relevances)):
        rep.append(item_relevances[i])
    df = calc_unfairness(position_attentions,true_attention,np.array(rep),f"Ranking[{i+1}]")
    results = results.append(df)
    
    #if single_averaged is None:
    #    single_averaged = df
    #else:
    #    single_averaged += df

#single_averaged = single_averaged / len(item_relevances)
results = results.append(single_averaged)
results = results.reset_index()
results

Category  Iteration  \
0     3. Closest Pair          0   
1     3. Closest Pair          1   
2     3. Closest Pair          2   
3     3. Closest Pair          3   
4     3. Closest Pair          4   
...               ...        ...   
5539      Ranking[72]         67   
5540      Ranking[72]         68   
5541      Ranking[72]         69   
5542      Ranking[72]         70   
5543      Ranking[72]         71   

                                             Unfairness  
0     [0.20762090864680013, 0.28969223253541776, 0.0...  
1     [0.41524181729360027, 0.5793844650708355, 0.16...  
2     [0.6228627259404004, 0.8690766976062534, 0.248...  
3     [0.8304836345872005, 1.158768930141671, 0.3315...  
4     [1.0381045432340006, 1.448461162677089, 0.4144...  
...                                                 ...  
5539  [19.76551050317537, 14.184660478749395, 5.3704...  
5540  [20.05617977528089, 14.393258426966298, 5.4494...  
5541  [20.346849047386407, 14.601856375183202, 5.528...  
5542  [20.637518319491928, 14.810454323400105, 5.607...  
5543  [20.92818759159745, 15.019052271617007, 5.6863...  

[5544 rows x 3 columns]

In [36]:
unfairness_results = pd.DataFrame(list(results['Unfairness']))
unfairness_results = unfairness_results.join(results)
unfairness_results = unfairness_results.drop('Unfairness',axis=1).melt(id_vars=['Category','Iteration'])
unfairness_results.columns = ["Category","Iteration","Item","Unfairness"]
unfairness_results

Category  Iteration Item  Unfairness
0      3. Closest Pair          0    0    0.207621
1      3. Closest Pair          1    0    0.415242
2      3. Closest Pair          2    0    0.622863
3      3. Closest Pair          3    0    0.830484
4      3. Closest Pair          4    0    1.038105
...                ...        ...  ...         ...
60979      Ranking[72]         67   10    5.625142
60980      Ranking[72]         68   10    5.707865
60981      Ranking[72]         69   10    5.790588
60982      Ranking[72]         70   10    5.873311
60983      Ranking[72]         71   10    5.956033

[60984 rows x 4 columns]

In [39]:
import altair as alt

source = unfairness_results.copy()
source['Method'] = source['Category'].apply(lambda v: v.split("[")[0]) #.str.split("[")[0]
source['Method'].loc[source['Method'] == 'Ranking'] = '1. Single Ranking'
source.loc[source['Method'] == '1. Single Ranking'].groupby('Iteration')['Unfairness'].mean()
added = source.loc[source['Method'] == '1. Single Ranking'].groupby('Iteration')['Unfairness'].mean().reset_index()
added['Method'] = '1. Single Ranking (Average)'
added['Category'] = added['Method'].copy()
source = source.append(added)
source = source.loc[source['Method'] != '1. Single Ranking']

alt.Chart(source).mark_line().encode(
    x=alt.X('Iteration',title='Iteration'),
    y=alt.Y('Unfairness',aggregate='average',title='Unfairness'),
    color="Method",
    detail='Category'
)

alt.Chart(...)

In [40]:
import altair as alt

source = unfairness_results.copy()
source['color'] = source['Category'].apply(lambda v: v.split("[")[0]) #.str.split("[")[0]

alt.Chart(source).mark_line().encode(
    x='Iteration',
    y='Unfairness',
    color="color",
    detail='Category',
    row='Item'
)

alt.Chart(...)

In [41]:
thetas = [0.75,1]
solutions = {}
unfairness = {}
for i in [0]:
    rep = []
    for j in range(len(item_relevances)):
        rep.append(item_relevances[i])
    pos_attentions = equity_of_attention.common.calc_position_attentions(len(item_relevances[0]), 
                                                                         click_probability=0.5,
                                                                         position_cutoff=len(item_relevances[0])//2)
    print(pos_attentions)
    for theta in thetas:
        solutions[theta], unfairness[theta] = equity_of_attention.common.model_3(rep,pos_attentions,theta=theta)

[0.5     0.25    0.125   0.0625  0.03125 0.      0.      0.      0.
 0.      0.     ]
0: tau=0.2727272727272727
1: tau=0.2
2: tau=0.2
3: tau=0.2727272727272727
4: tau=0.23636363636363636
5: tau=0.38181818181818183
6: tau=0.5636363636363636
7: tau=0.4909090909090909
8: tau=0.4909090909090909
9: tau=0.7090909090909091
10: tau=0.5272727272727272
11: tau=0.41818181818181815
12: tau=0.7090909090909091
13: tau=0.5272727272727272
14: tau=0.34545454545454546
15: tau=0.6363636363636364
16: tau=0.6363636363636364
17: tau=0.6000000000000001
18: tau=0.5636363636363636
19: tau=0.5636363636363636
20: tau=0.38181818181818183
21: tau=0.4909090909090909
22: tau=0.5636363636363636
23: tau=0.38181818181818183
24: tau=0.7454545454545454
25: tau=0.38181818181818183
26: tau=0.6363636363636364
27: tau=0.34545454545454546
28: tau=0.45454545454545453
29: tau=0.4909090909090909
30: tau=0.6000000000000001
31: tau=0.45454545454545453
32: tau=0.4909090909090909
33: tau=0.6000000000000001
34: tau=0.2727272727272727

In [42]:
#pair_item_relevances
pos_attentions = equity_of_attention.common.calc_position_attentions(len(pair_item_relevances[0]), 
                                                                     click_probability=0.5,
                                                                     position_cutoff=len(pair_item_relevances[0])//2)
pair_solutions = {}
pair_unfairness = {}
print(pos_attentions)
for theta in thetas:
    pair_solutions[theta], pair_unfairness[theta] = equity_of_attention.common.model_3(pair_item_relevances,pos_attentions,theta=theta)

[0.5     0.25    0.125   0.0625  0.03125 0.      0.      0.      0.
 0.      0.     ]
0: tau=0.4909090909090909
1: tau=0.2727272727272727
2: tau=0.2727272727272727
3: tau=0.45454545454545453
4: tau=0.5636363636363636
5: tau=0.38181818181818183
6: tau=0.5272727272727272
7: tau=0.3090909090909091
8: tau=0.5636363636363636
9: tau=0.4909090909090909
10: tau=0.16363636363636364
11: tau=0.05454545454545454
12: tau=0.3090909090909091
13: tau=0.2727272727272727
14: tau=0.23636363636363636
15: tau=0.6363636363636364
16: tau=0.45454545454545453
17: tau=0.6363636363636364
18: tau=0.45454545454545453
19: tau=0.2
20: tau=0.1272727272727273
21: tau=0.2727272727272727
22: tau=0.6363636363636364
23: tau=0.4909090909090909
24: tau=0.7090909090909091
25: tau=0.7454545454545454
26: tau=0.34545454545454546
27: tau=0.5636363636363636
28: tau=0.45454545454545453
29: tau=0.4909090909090909
30: tau=0.6363636363636364
31: tau=0.5272727272727272
32: tau=0.5636363636363636
33: tau=0.38181818181818183
34: tau=0.5

In [43]:
pair_unfairness_df = pd.DataFrame(pair_unfairness)
pair_unfairness_df.index.name = 'Iteration'
pair_unfairness_df = pair_unfairness_df.reset_index().melt(id_vars=['Iteration'])
pair_unfairness_df.columns = ["Iteration","theta",'unfairness']
pair_unfairness_df['Category'] = 'Pair'
pair_unfairness_df

Iteration theta  unfairness Category
0            0  0.75    1.222874     Pair
1            1  0.75    1.832845     Pair
2            2  0.75    1.503421     Pair
3            3  0.75    1.880743     Pair
4            4  0.75    2.455523     Pair
..         ...   ...         ...      ...
139         67   1.0   57.017595     Pair
140         68   1.0   57.812317     Pair
141         69   1.0   58.701857     Pair
142         70   1.0   59.462366     Pair
143         71   1.0   60.222874     Pair

[144 rows x 4 columns]

In [44]:
unfairness_df = pd.DataFrame(unfairness)
unfairness_df.index.name = 'Iteration'
unfairness_df = unfairness_df.reset_index().melt(id_vars=['Iteration'])
unfairness_df.columns = ["Iteration","theta",'unfairness']
unfairness_df['Category'] = 'Ranking[0]'
unfairness_df

Iteration theta  unfairness    Category
0            0  0.75    1.291300  Ranking[0]
1            1  0.75    1.843597  Ranking[0]
2            2  0.75    2.387097  Ranking[0]
3            3  0.75    2.995112  Ranking[0]
4            4  0.75    3.802542  Ranking[0]
..         ...   ...         ...         ...
139         67   1.0   84.684262  Ranking[0]
140         68   1.0   85.929619  Ranking[0]
141         69   1.0   87.174976  Ranking[0]
142         70   1.0   88.420332  Ranking[0]
143         71   1.0   89.665689  Ranking[0]

[144 rows x 4 columns]

In [45]:
source = unfairness_df.append(pair_unfairness_df)
source['Group'] = source['Category'] + ", theta=" + source['theta'].astype(str)
source

Iteration theta  unfairness    Category                   Group
0            0  0.75    1.291300  Ranking[0]  Ranking[0], theta=0.75
1            1  0.75    1.843597  Ranking[0]  Ranking[0], theta=0.75
2            2  0.75    2.387097  Ranking[0]  Ranking[0], theta=0.75
3            3  0.75    2.995112  Ranking[0]  Ranking[0], theta=0.75
4            4  0.75    3.802542  Ranking[0]  Ranking[0], theta=0.75
..         ...   ...         ...         ...                     ...
139         67   1.0   57.017595        Pair         Pair, theta=1.0
140         68   1.0   57.812317        Pair         Pair, theta=1.0
141         69   1.0   58.701857        Pair         Pair, theta=1.0
142         70   1.0   59.462366        Pair         Pair, theta=1.0
143         71   1.0   60.222874        Pair         Pair, theta=1.0

[288 rows x 5 columns]

In [46]:
alt.Chart(source).mark_line().encode(
    x='Iteration',
    y='unfairness',
    color="Group:N"
)

alt.Chart(...)